In [1]:
import pandas as pd
import numpy as np

from datetime import datetime

%matplotlib inline
import matplotlib as mpl
import matplotlib.pyplot as plt

import seaborn as sns


sns.set(style="darkgrid")

mpl.rcParams['figure.figsize'] = (16, 9)
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', None)

from scipy import optimize
from scipy import integrate

# Data preparation of countries

In [2]:
# try to parse the dates right at the beginning 
# it works out of the box if the date was stored ISO YYYY-MM-DD format

COVID_data_path='../ads_covid-19/data/raw/COVID-19/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_global.csv'
df_data = pd.read_csv(COVID_data_path)
df_data.head()

#df_analyse=pd.read_csv('../ads_covid-19/data/processed/COVID_small_flat_table.csv',sep=';')  
#df_analyse.sort_values('date',ascending=True)

Province/State Country/Region       Lat       Long  1/22/20  1/23/20  \
0            NaN    Afghanistan  33.93911  67.709953        0        0   
1            NaN        Albania  41.15330  20.168300        0        0   
2            NaN        Algeria  28.03390   1.659600        0        0   
3            NaN        Andorra  42.50630   1.521800        0        0   
4            NaN         Angola -11.20270  17.873900        0        0   

   1/24/20  1/25/20  1/26/20  1/27/20  1/28/20  1/29/20  1/30/20  1/31/20  \
0        0        0        0        0        0        0        0        0   
1        0        0        0        0        0        0        0        0   
2        0        0        0        0        0        0        0        0   
3        0        0        0        0        0        0        0        0   
4        0        0        0        0        0        0        0        0   

   2/1/20  2/2/20  2/3/20  2/4/20  2/5/20  2/6/20  2/7/20  2/8/20  2/9/20  \
0       0       0       0       0       0       0       0       0       0   
1       0       0       0       0       0       0       0       0       0   
2       0       0       0       0       0       0       0       0       0   
3       0       0       0       0       0       0       0       0       0   
4       0       0       0       0       0       0       0       0       0   

   2/10/20  2/11/20  2/12/20  2/13/20  2/14/20  2/15/20  2/16/20  2/17/20  \
0        0        0        0        0        0        0        0        0   
1        0        0        0        0        0        0        0        0   
2        0        0        0        0        0        0        0        0   
3        0        0        0        0        0        0        0        0   
4        0        0        0        0        0        0        0        0   

   2/18/20  2/19/20  2/20/20  2/21/20  2/22/20  2/23/20  2/24/20  2/25/20  \
0        0        0        0        0        0        0        1        1   
1        0        0        0        0        0        0        0        0   
2        0        0        0        0        0        0        0        1   
3        0        0        0        0        0        0        0        0   
4        0        0        0        0        0        0        0        0   

   2/26/20  2/27/20  2/28/20  2/29/20  3/1/20  3/2/20  3/3/20  3/4/20  3/5/20  \
0        1        1        1        1       1       1       1       1       1   
1        0        0        0        0       0       0       0       0       0   
2        1        1        1        1       1       3       5      12      12   
3        0        0        0        0       0       1       1       1       1   
4        0        0        0        0       0       0       0       0       0   

   3/6/20  3/7/20  3/8/20  3/9/20  3/10/20  3/11/20  3/12/20  3/13/20  \
0       1       1       4       4        5        7        7        7   
1       0       0       0       2       10       12       23       33   
2      17      17      19      20       20       20       24       26   
3       1       1       1       1        1        1        1        1   
4       0       0       0       0        0        0        0        0   

   3/14/20  3/15/20  3/16/20  3/17/20  3/18/20  3/19/20  3/20/20  3/21/20  \
0       11       16       21       22       22       22       24       24   
1       38       42       51       55       59       64       70       76   
2       37       48       54       60       74       87       90      139   
3        1        1        2       39       39       53       75       88   
4        0        0        0        0        0        0        1        2   

   3/22/20  3/23/20  3/24/20  3/25/20  3/26/20  3/27/20  3/28/20  3/29/20  \
0       40       40       74       84       94      110      110      120   
1       89      104      123      146      174      186      197      212   
2      201      230      264      302      367      409      454      511   
3      1

In [3]:
df_data = df_data.drop(['Lat','Long'],axis=1)
df_data.head()

Province/State Country/Region  1/22/20  1/23/20  1/24/20  1/25/20  1/26/20  \
0            NaN    Afghanistan        0        0        0        0        0   
1            NaN        Albania        0        0        0        0        0   
2            NaN        Algeria        0        0        0        0        0   
3            NaN        Andorra        0        0        0        0        0   
4            NaN         Angola        0        0        0        0        0   

   1/27/20  1/28/20  1/29/20  1/30/20  1/31/20  2/1/20  2/2/20  2/3/20  \
0        0        0        0        0        0       0       0       0   
1        0        0        0        0        0       0       0       0   
2        0        0        0        0        0       0       0       0   
3        0        0        0        0        0       0       0       0   
4        0        0        0        0        0       0       0       0   

   2/4/20  2/5/20  2/6/20  2/7/20  2/8/20  2/9/20  2/10/20  2/11/20  2/12/20  \
0       0       0       0       0       0       0        0        0        0   
1       0       0       0       0       0       0        0        0        0   
2       0       0       0       0       0       0        0        0        0   
3       0       0       0       0       0       0        0        0        0   
4       0       0       0       0       0       0        0        0        0   

   2/13/20  2/14/20  2/15/20  2/16/20  2/17/20  2/18/20  2/19/20  2/20/20  \
0        0        0        0        0        0        0        0        0   
1        0        0        0        0        0        0        0        0   
2        0        0        0        0        0        0        0        0   
3        0        0        0        0        0        0        0        0   
4        0        0        0        0        0        0        0        0   

   2/21/20  2/22/20  2/23/20  2/24/20  2/25/20  2/26/20  2/27/20  2/28/20  \
0        0        0        0        1        1        1        1        1   
1        0        0        0        0        0        0        0        0   
2        0        0        0        0        1        1        1        1   
3        0        0        0        0        0        0        0        0   
4        0        0        0        0        0        0        0        0   

   2/29/20  3/1/20  3/2/20  3/3/20  3/4/20  3/5/20  3/6/20  3/7/20  3/8/20  \
0        1       1       1       1       1       1       1       1       4   
1        0       0       0       0       0       0       0       0       0   
2        1       1       3       5      12      12      17      17      19   
3        0       0       1       1       1       1       1       1       1   
4        0       0       0       0       0       0       0       0       0   

   3/9/20  3/10/20  3/11/20  3/12/20  3/13/20  3/14/20  3/15/20  3/16/20  \
0       4        5        7        7        7       11       16       21   
1       2       10       12       23       33       38       42       51   
2      20       20       20       24       26       37       48       54   
3       1        1        1        1        1        1        1        2   
4       0        0        0        0        0        0        0        0   

   3/17/20  3/18/20  3/19/20  3/20/20  3/21/20  3/22/20  3/23/20  3/24/20  \
0       22       22       22       24       24       40       40       74   
1       55       59       64       70       76       89      104      123   
2       60       74       87       90      139      201      230      264   
3       39       39       53       75       88      113      133      164   
4        0        0        0        1        2        2        3        3   

   3/25/20  3/26/20  3/27/20  3/28/20  3/29/20  3/30/20  3/31/20  4/1/20  \
0       84       94      110      110      120      170      174     237   
1      146      174      186      197      212      223      243     259   
2      302      367      409      454      511      

In [4]:
df_data = df_data.rename(columns={'Country/Region':'country',
                                   'Province/State':'state'})
df_data['state'] = df_data['state'].fillna('no')
df_data.head()

state      country  1/22/20  1/23/20  1/24/20  1/25/20  1/26/20  1/27/20  \
0    no  Afghanistan        0        0        0        0        0        0   
1    no      Albania        0        0        0        0        0        0   
2    no      Algeria        0        0        0        0        0        0   
3    no      Andorra        0        0        0        0        0        0   
4    no       Angola        0        0        0        0        0        0   

   1/28/20  1/29/20  1/30/20  1/31/20  2/1/20  2/2/20  2/3/20  2/4/20  2/5/20  \
0        0        0        0        0       0       0       0       0       0   
1        0        0        0        0       0       0       0       0       0   
2        0        0        0        0       0       0       0       0       0   
3        0        0        0        0       0       0       0       0       0   
4        0        0        0        0       0       0       0       0       0   

   2/6/20  2/7/20  2/8/20  2/9/20  2/10/20  2/11/20  2/12/20  2/13/20  \
0       0       0       0       0        0        0        0        0   
1       0       0       0       0        0        0        0        0   
2       0       0       0       0        0        0        0        0   
3       0       0       0       0        0        0        0        0   
4       0       0       0       0        0        0        0        0   

   2/14/20  2/15/20  2/16/20  2/17/20  2/18/20  2/19/20  2/20/20  2/21/20  \
0        0        0        0        0        0        0        0        0   
1        0        0        0        0        0        0        0        0   
2        0        0        0        0        0        0        0        0   
3        0        0        0        0        0        0        0        0   
4        0        0        0        0        0        0        0        0   

   2/22/20  2/23/20  2/24/20  2/25/20  2/26/20  2/27/20  2/28/20  2/29/20  \
0        0        0        1        1        1        1        1        1   
1        0        0        0        0        0        0        0        0   
2        0        0        0        1        1        1        1        1   
3        0        0        0        0        0        0        0        0   
4        0        0        0        0        0        0        0        0   

   3/1/20  3/2/20  3/3/20  3/4/20  3/5/20  3/6/20  3/7/20  3/8/20  3/9/20  \
0       1       1       1       1       1       1       1       4       4   
1       0       0       0       0       0       0       0       0       2   
2       1       3       5      12      12      17      17      19      20   
3       0       1       1       1       1       1       1       1       1   
4       0       0       0       0       0       0       0       0       0   

   3/10/20  3/11/20  3/12/20  3/13/20  3/14/20  3/15/20  3/16/20  3/17/20  \
0        5        7        7        7       11       16       21       22   
1       10       12       23       33       38       42       51       55   
2       20       20       24       26       37       48       54       60   
3        1        1        1        1        1        1        2       39   
4        0        0        0        0        0        0        0        0   

   3/18/20  3/19/20  3/20/20  3/21/20  3/22/20  3/23/20  3/24/20  3/25/20  \
0       22       22       24       24       40       40       74       84   
1       59       64       70       76       89      104      123      146   
2       74       87       90      139      201      230      264      302   
3       39       53       75       88      113      133      164      188   
4        0        0        1        2        2        3        3        3   

   3/26/20  3/27/20  3/28/20  3/29/20  3/30/20  3/31/20  4/1/20  4/2/20  \
0       94      110      110      120      170      174     237     273   
1      174      186      197      212      223      243     259     277   
2      367      409      454      511      584      716     847    

In [5]:
full_country_list = df_data['country'].unique().tolist()
full_country_list

['Afghanistan',
 'Albania',
 'Algeria',
 'Andorra',
 'Angola',
 'Antigua and Barbuda',
 'Argentina',
 'Armenia',
 'Australia',
 'Austria',
 'Azerbaijan',
 'Bahamas',
 'Bahrain',
 'Bangladesh',
 'Barbados',
 'Belarus',
 'Belgium',
 'Belize',
 'Benin',
 'Bhutan',
 'Bolivia',
 'Bosnia and Herzegovina',
 'Botswana',
 'Brazil',
 'Brunei',
 'Bulgaria',
 'Burkina Faso',
 'Burma',
 'Burundi',
 'Cabo Verde',
 'Cambodia',
 'Cameroon',
 'Canada',
 'Central African Republic',
 'Chad',
 'Chile',
 'China',
 'Colombia',
 'Comoros',
 'Congo (Brazzaville)',
 'Congo (Kinshasa)',
 'Costa Rica',
 "Cote d'Ivoire",
 'Croatia',
 'Cuba',
 'Cyprus',
 'Czechia',
 'Denmark',
 'Diamond Princess',
 'Djibouti',
 'Dominica',
 'Dominican Republic',
 'Ecuador',
 'Egypt',
 'El Salvador',
 'Equatorial Guinea',
 'Eritrea',
 'Estonia',
 'Eswatini',
 'Ethiopia',
 'Fiji',
 'Finland',
 'France',
 'Gabon',
 'Gambia',
 'Georgia',
 'Germany',
 'Ghana',
 'Greece',
 'Grenada',
 'Guatemala',
 'Guinea',
 'Guinea-Bissau',
 'Guyana',

In [6]:
time_idx = df_data.columns[2:]

In [7]:
df_analyse = pd.DataFrame({
    'date':time_idx})
df_analyse.head()

date
0  1/22/20
1  1/23/20
2  1/24/20
3  1/25/20
4  1/26/20

In [8]:
for each in full_country_list:
    df_analyse[each] = np.array(df_data[df_data['country']==each].iloc[:,2::].sum(axis=0))

In [9]:
df_analyse.head()

date  Afghanistan  Albania  Algeria  Andorra  Angola  \
0  1/22/20            0        0        0        0       0   
1  1/23/20            0        0        0        0       0   
2  1/24/20            0        0        0        0       0   
3  1/25/20            0        0        0        0       0   
4  1/26/20            0        0        0        0       0   

   Antigua and Barbuda  Argentina  Armenia  Australia  Austria  Azerbaijan  \
0                    0          0        0          0        0           0   
1                    0          0        0          0        0           0   
2                    0          0        0          0        0           0   
3                    0          0        0          0        0           0   
4                    0          0        0          4        0           0   

   Bahamas  Bahrain  Bangladesh  Barbados  Belarus  Belgium  Belize  Benin  \
0        0        0           0         0        0        0       0      0   
1        0        0           0         0        0        0       0      0   
2        0        0           0         0        0        0       0      0   
3        0        0           0         0        0        0       0      0   
4        0        0           0         0        0        0       0      0   

   Bhutan  Bolivia  Bosnia and Herzegovina  Botswana  Brazil  Brunei  \
0       0        0                       0         0       0       0   
1       0        0                       0         0       0       0   
2       0        0                       0         0       0       0   
3       0        0                       0         0       0       0   
4       0        0                       0         0       0       0   

   Bulgaria  Burkina Faso  Burma  Burundi  Cabo Verde  Cambodia  Cameroon  \
0         0             0      0        0           0         0         0   
1         0             0      0        0           0         0         0   
2         0             0      0        0           0         0         0   
3         0             0      0        0           0         0         0   
4         0             0      0        0           0         0         0   

   Canada  Central African Republic  Chad  Chile  China  Colombia  Comoros  \
0       0                         0     0      0    548         0        0   
1       0                         0     0      0    643         0        0   
2       0                         0     0      0    920         0        0   
3       0                         0     0      0   1406         0        0   
4       1                         0     0      0   2075         0        0   

   Congo (Brazzaville)  Congo (Kinshasa)  Costa Rica  Cote d'Ivoire  Croatia  \
0                    0                 0           0              0        0   
1                    0                 0           0              0        0   
2                    0                 0           0              0        0   
3                    0                 0           0              0        0   
4                    0                 0           0              0        0   

   Cuba  Cyprus  Czechia  Denmark  Diamond Princess  Djibouti  Dominica  \
0     0       0        0        0                 0         0         0   
1     0       0        0        0                 0         0         0   
2     0       0        0        0                 0         0         0   
3     0       0        0        0                 0         0         0   
4     0       0        0        0                 0         0         0   

   Dominican Republic  Ecuador  Egypt  El Salvador  Equatorial Guinea  \
0                   0        0      0            0                  0   
1                   0        0      0            0                  0   
2                   0        0      0            0                  0   
3                   0        0      0            0                  0   
4                   0        0   

In [10]:
time_idx=[datetime.strptime(each,"%m/%d/%y") for each in df_analyse.date] # convert to datetime
time_str=[each.strftime('%y-%m-%d') for each in time_idx] # convert back to date ISO norm (str)
df_analyse['date']=time_idx # doubt: whether to assign time_str

In [11]:
df_analyse

date  Afghanistan  Albania  Algeria  Andorra  Angola  \
0   2020-01-22            0        0        0        0       0   
1   2020-01-23            0        0        0        0       0   
2   2020-01-24            0        0        0        0       0   
3   2020-01-25            0        0        0        0       0   
4   2020-01-26            0        0        0        0       0   
5   2020-01-27            0        0        0        0       0   
6   2020-01-28            0        0        0        0       0   
7   2020-01-29            0        0        0        0       0   
8   2020-01-30            0        0        0        0       0   
9   2020-01-31            0        0        0        0       0   
10  2020-02-01            0        0        0        0       0   
11  2020-02-02            0        0        0        0       0   
12  2020-02-03            0        0        0        0       0   
13  2020-02-04            0        0        0        0       0   
14  2020-02-05            0        0        0        0       0   
15  2020-02-06            0        0        0        0       0   
16  2020-02-07            0        0        0        0       0   
17  2020-02-08            0        0        0        0       0   
18  2020-02-09            0        0        0        0       0   
19  2020-02-10            0        0        0        0       0   
20  2020-02-11            0        0        0        0       0   
21  2020-02-12            0        0        0        0       0   
22  2020-02-13            0        0        0        0       0   
23  2020-02-14            0        0        0        0       0   
24  2020-02-15            0        0        0        0       0   
25  2020-02-16            0        0        0        0       0   
26  2020-02-17            0        0        0        0       0   
27  2020-02-18            0        0        0        0       0   
28  2020-02-19            0        0        0        0       0   
29  2020-02-20            0        0        0        0       0   
30  2020-02-21            0        0        0        0       0   
31  2020-02-22            0        0        0        0       0   
32  2020-02-23            0        0        0        0       0   
33  2020-02-24            1        0        0        0       0   
34  2020-02-25            1        0        1        0       0   
35  2020-02-26            1        0        1        0       0   
36  2020-02-27            1        0        1        0       0   
37  2020-02-28            1        0        1        0       0   
38  2020-02-29            1        0        1        0       0   
39  2020-03-01            1        0        1        0       0   
40  2020-03-02            1        0        3        1       0   
41  2020-03-03            1        0        5        1       0   
42  2020-03-04            1        0       12        1       0   
43  2020-03-05            1        0       12        1       0   
44  2020-03-06            1        0       17        1       0   
45  2020-03-07            1        0       17        1       0   
46  2020-03-08            4        0       19        1       0   
47  2020-03-09            4        2       20        1       0   
48  2020-03-10            5       10       20        1       0   
49  2020-03-11            7       12       20        1       0   
50  2020-03-12            7       23       24        1       0   
51  2020-03-13            7       33       26        1       0   
52  2020-03-14           11       38       37        1       0   
53  2020-03-15           16       42       48        1       0   
54  2020-03-16           21       51       54        2       0   
55  2020-03-17           22       55       60       39       0   
56  2020-03-18           22       59       74       39       0   
57  2020-03-19           22       64       87       53       0   
58  2020-03-20           24       70       90       75       1   
59  2020-03-21           24       76      139     

In [12]:
df_analyse.to_csv('../ads_covid-19/data/processed/all_country_flat_table.csv', sep=';',index=False)

In [13]:
df_analys = pd.read_csv('../ads_covid-19/data/processed/all_country_flat_table.csv',sep=';',parse_dates=[0])

In [14]:
df_analys.head()

date  Afghanistan  Albania  Algeria  Andorra  Angola  \
0 2020-01-22            0        0        0        0       0   
1 2020-01-23            0        0        0        0       0   
2 2020-01-24            0        0        0        0       0   
3 2020-01-25            0        0        0        0       0   
4 2020-01-26            0        0        0        0       0   

   Antigua and Barbuda  Argentina  Armenia  Australia  Austria  Azerbaijan  \
0                    0          0        0          0        0           0   
1                    0          0        0          0        0           0   
2                    0          0        0          0        0           0   
3                    0          0        0          0        0           0   
4                    0          0        0          4        0           0   

   Bahamas  Bahrain  Bangladesh  Barbados  Belarus  Belgium  Belize  Benin  \
0        0        0           0         0        0        0       0      0   
1        0        0           0         0        0        0       0      0   
2        0        0           0         0        0        0       0      0   
3        0        0           0         0        0        0       0      0   
4        0        0           0         0        0        0       0      0   

   Bhutan  Bolivia  Bosnia and Herzegovina  Botswana  Brazil  Brunei  \
0       0        0                       0         0       0       0   
1       0        0                       0         0       0       0   
2       0        0                       0         0       0       0   
3       0        0                       0         0       0       0   
4       0        0                       0         0       0       0   

   Bulgaria  Burkina Faso  Burma  Burundi  Cabo Verde  Cambodia  Cameroon  \
0         0             0      0        0           0         0         0   
1         0             0      0        0           0         0         0   
2         0             0      0        0           0         0         0   
3         0             0      0        0           0         0         0   
4         0             0      0        0           0         0         0   

   Canada  Central African Republic  Chad  Chile  China  Colombia  Comoros  \
0       0                         0     0      0    548         0        0   
1       0                         0     0      0    643         0        0   
2       0                         0     0      0    920         0        0   
3       0                         0     0      0   1406         0        0   
4       1                         0     0      0   2075         0        0   

   Congo (Brazzaville)  Congo (Kinshasa)  Costa Rica  Cote d'Ivoire  Croatia  \
0                    0                 0           0              0        0   
1                    0                 0           0              0        0   
2                    0                 0           0              0        0   
3                    0                 0           0              0        0   
4                    0                 0           0              0        0   

   Cuba  Cyprus  Czechia  Denmark  Diamond Princess  Djibouti  Dominica  \
0     0       0        0        0                 0         0         0   
1     0       0        0        0                 0         0         0   
2     0       0        0        0                 0         0         0   
3     0       0        0        0                 0         0         0   
4     0       0        0        0                 0         0         0   

   Dominican Republic  Ecuador  Egypt  El Salvador  Equatorial Guinea  \
0                   0        0      0            0                  0   
1                   0        0      0            0                  0   
2                   0        0      0            0                  0   
3                   0        0      0            0                  0   
4                   0  

# Population Data

In [15]:
population_df = pd.read_csv('../ads_covid-19/data/raw/population_data.csv',sep=';', thousands=',')  

In [16]:
population_df

country  population
0                         Afghanistan    38928346
1                             Albania     2877797
2                             Algeria    43851044
3                      American Samoa       55191
4                             Andorra       77265
5                              Angola    32866272
6                            Anguilla       15003
7                 Antigua and Barbuda       97929
8                           Argentina    45195774
9                             Armenia     2963243
10                              Aruba      106766
11                          Australia    25499884
12                            Austria     9006398
13                         Azerbaijan    10139177
14                            Bahamas      393244
15                            Bahrain     1701575
16                         Bangladesh   164689383
17                           Barbados      287375
18                            Belarus     9449323
19                            Belgium    11589623
20                             Belize      397628
21                              Benin    12123200
22                            Bermuda       62278
23                             Bhutan      771608
24                            Bolivia    11673021
25             Bosnia and Herzegovina     3280819
26                           Botswana     2351627
27                             Brazil   212559417
28             British Virgin Islands       30231
29                             Brunei      437479
30                           Bulgaria     6948445
31                       Burkina Faso    20903273
32                              Burma    54409800
33                            Burundi    11890784
34                         Cabo Verde      555987
35                           Cambodia    16718965
36                           Cameroon    26545863
37                             Canada    37742154
38              Caribbean Netherlands       26223
39                     Cayman Islands       65722
40           Central African Republic     4829767
41                               Chad    16425864
42                    Channel Islands      173863
43                              Chile    19116201
44                              China  1439323776
45                           Colombia    50882891
46                            Comoros      869601
47                Congo (Brazzaville)     5518087
48                   Congo (Kinshasa)    89561403
49                       Cook Islands       17564
50                         Costa Rica     5094118
51                      Cote d'Ivoire    26378274
52                            Croatia     4105267
53                               Cuba    11326616
54                            Curaçao      164093
55                             Cyprus     1207359
56                            Czechia    10708981
57                            Denmark     5792202
58                   Diamond Princess        3711
59                           Djibouti      988000
60                           Dominica       71986
61                 Dominican Republic    10847910
62                            Ecuador    17643054
63                              Egypt   102334404
64                        El Salvador     6486205
65                  Equatorial Guinea     1402985
66                            Eritrea     3546421
67                            Estonia     1326535
68                           Eswatini     1160164
69                           Ethiopia   114963588
70                     Faeroe Islands       48863
71                   Falkland Islands        3480
72                               Fiji      896445
73                            Finland     5540720
74                             France    65273511
75                      French Guiana      298682
76                   French Polynesia      280908
77                              Gabon     2225734
78                             Gambia     2416668
79                            

In [17]:
population_df = population_df.set_index(['country']).T
#population_df = population_df.T
population_df

country     Afghanistan  Albania   Algeria  American Samoa  Andorra    Angola  \
population     38928346  2877797  43851044           55191    77265  32866272   

country     Anguilla  Antigua and Barbuda  Argentina  Armenia   Aruba  \
population     15003                97929   45195774  2963243  106766   

country     Australia  Austria  Azerbaijan  Bahamas  Bahrain  Bangladesh  \
population   25499884  9006398    10139177   393244  1701575   164689383   

country     Barbados  Belarus   Belgium  Belize     Benin  Bermuda  Bhutan  \
population    287375  9449323  11589623  397628  12123200    62278  771608   

country      Bolivia  Bosnia and Herzegovina  Botswana     Brazil  \
population  11673021                 3280819   2351627  212559417   

country     British Virgin Islands  Brunei  Bulgaria  Burkina Faso     Burma  \
population                   30231  437479   6948445      20903273  54409800   

country      Burundi  Cabo Verde  Cambodia  Cameroon    Canada  \
population  11890784      555987  16718965  26545863  37742154   

country     Caribbean Netherlands  Cayman Islands  Central African Republic  \
population                  26223           65722                   4829767   

country         Chad  Channel Islands     Chile       China  Colombia  \
population  16425864           173863  19116201  1439323776  50882891   

country     Comoros  Congo (Brazzaville)  Congo (Kinshasa)  Cook Islands  \
population   869601              5518087          89561403         17564   

country     Costa Rica  Cote d'Ivoire  Croatia      Cuba  Curaçao   Cyprus  \
population     5094118       26378274  4105267  11326616   164093  1207359   

country      Czechia  Denmark  Diamond Princess  Djibouti  Dominica  \
population  10708981  5792202              3711    988000     71986   

country     Dominican Republic   Ecuador      Egypt  El Salvador  \
population            10847910  17643054  102334404      6486205   

country     Equatorial Guinea  Eritrea  Estonia  Eswatini   Ethiopia  \
population            1402985  3546421  1326535   1160164  114963588   

country     Faeroe Islands  Falkland Islands    Fiji  Finland    France  \
population           48863              3480  896445  5540720  65273511   

country     French Guiana  French Polynesia    Gabon   Gambia  Georgia  \
population         298682            280908  2225734  2416668  3989167   

country      Germany     Ghana  Gibraltar    Greece  Greenland  Grenada  \
population  83783942  31072940      33691  10423054      56770   112523   

country     Guadeloupe    Guam  Guatemala    Guinea  Guinea-Bissau  Guyana  \
population      400124  168775   17915568  13132795        1968001  786552   

country        Haiti  Holy See  Honduras  Hong Kong  Hungary  Iceland  \
population  11402528       801   9904607    7496981  9660351   341243   

country          India  Indonesia      Iran      Iraq  Ireland  Isle of Man  \
population  1380004385  273523615  83992949  40222493  4937786        85033   

country      Israel     Italy  Jamaica      Japan    Jordan  Kazakhstan  \
population  8655535  60461826  2961167  126476461  10203134    18776707   

country        Kenya  Kiribati  Korea, South   Kosovo   Kuwait  Kyrgyzstan  \
population  53771296    119449      51269185  1845000  4270571     6524195   

country        Laos   Latvia  Lebanon  Lesotho  Liberia    Libya  \
population  7275560  1886198  6825445  2142249  5057681  6871292   

country     Liechtenstein  Lithuania  Luxembourg  MS Zaandam   Macao  \
population          38128    2722289      625978        1432  649335   

country     Madagascar    Malawi  Malaysia  Maldives      Mali   Malta  \
population    27691018  19129952  32365999    540544  20250833  441543   

country     Marshall Islands  Martinique  Mauritania  Mauritius  Mayotte  \
population             59190      375265     4649658    1271768   272815   

country        Mexico  Micronesia  Moldova  Monaco  Mongolia  Montenegro  \
population  128932753   

In [18]:
country_list = df_analyse.columns[1:]
country_list

Index(['Afghanistan', 'Albania', 'Algeria', 'Andorra', 'Angola',
       'Antigua and Barbuda', 'Argentina', 'Armenia', 'Australia', 'Austria',
       ...
       'United Kingdom', 'Uruguay', 'Uzbekistan', 'Venezuela', 'Vietnam',
       'West Bank and Gaza', 'Western Sahara', 'Yemen', 'Zambia', 'Zimbabwe'],
      dtype='object', length=188)

# Fitting the parameters SIR model

In [19]:
for column in df_analyse.columns[1:]:
    print(column)

Afghanistan
Albania
Algeria
Andorra
Angola
Antigua and Barbuda
Argentina
Armenia
Australia
Austria
Azerbaijan
Bahamas
Bahrain
Bangladesh
Barbados
Belarus
Belgium
Belize
Benin
Bhutan
Bolivia
Bosnia and Herzegovina
Botswana
Brazil
Brunei
Bulgaria
Burkina Faso
Burma
Burundi
Cabo Verde
Cambodia
Cameroon
Canada
Central African Republic
Chad
Chile
China
Colombia
Comoros
Congo (Brazzaville)
Congo (Kinshasa)
Costa Rica
Cote d'Ivoire
Croatia
Cuba
Cyprus
Czechia
Denmark
Diamond Princess
Djibouti
Dominica
Dominican Republic
Ecuador
Egypt
El Salvador
Equatorial Guinea
Eritrea
Estonia
Eswatini
Ethiopia
Fiji
Finland
France
Gabon
Gambia
Georgia
Germany
Ghana
Greece
Grenada
Guatemala
Guinea
Guinea-Bissau
Guyana
Haiti
Holy See
Honduras
Hungary
Iceland
India
Indonesia
Iran
Iraq
Ireland
Israel
Italy
Jamaica
Japan
Jordan
Kazakhstan
Kenya
Korea, South
Kosovo
Kuwait
Kyrgyzstan
Laos
Latvia
Lebanon
Lesotho
Liberia
Libya
Liechtenstein
Lithuania
Luxembourg
MS Zaandam
Madagascar
Malawi
Malaysia
Maldives
Mali
Mal

In [20]:
data_y = []
t=[]
#for column in df_analyse.columns[1:]:
#for pos,column in enumerate(df_analyse.columns[1:]):
for column in df_analyse.columns:
        #data = np.array(df_analyse[column][50:])
    data_y.append(np.array(df_analyse[column][75:]))
    #t.append(np.arange(len(ydata)))
t = np.arange(len(data_y))

In [21]:
data_y

[array(['2020-04-06T00:00:00.000000000', '2020-04-07T00:00:00.000000000',
        '2020-04-08T00:00:00.000000000', '2020-04-09T00:00:00.000000000',
        '2020-04-10T00:00:00.000000000', '2020-04-11T00:00:00.000000000',
        '2020-04-12T00:00:00.000000000', '2020-04-13T00:00:00.000000000',
        '2020-04-14T00:00:00.000000000', '2020-04-15T00:00:00.000000000',
        '2020-04-16T00:00:00.000000000', '2020-04-17T00:00:00.000000000',
        '2020-04-18T00:00:00.000000000', '2020-04-19T00:00:00.000000000',
        '2020-04-20T00:00:00.000000000', '2020-04-21T00:00:00.000000000',
        '2020-04-22T00:00:00.000000000', '2020-04-23T00:00:00.000000000',
        '2020-04-24T00:00:00.000000000', '2020-04-25T00:00:00.000000000',
        '2020-04-26T00:00:00.000000000', '2020-04-27T00:00:00.000000000',
        '2020-04-28T00:00:00.000000000', '2020-04-29T00:00:00.000000000',
        '2020-04-30T00:00:00.000000000', '2020-05-01T00:00:00.000000000',
        '2020-05-02T00:00:00.000000000

In [22]:
t

array([  0,   1,   2,   3,   4,   5,   6,   7,   8,   9,  10,  11,  12,
        13,  14,  15,  16,  17,  18,  19,  20,  21,  22,  23,  24,  25,
        26,  27,  28,  29,  30,  31,  32,  33,  34,  35,  36,  37,  38,
        39,  40,  41,  42,  43,  44,  45,  46,  47,  48,  49,  50,  51,
        52,  53,  54,  55,  56,  57,  58,  59,  60,  61,  62,  63,  64,
        65,  66,  67,  68,  69,  70,  71,  72,  73,  74,  75,  76,  77,
        78,  79,  80,  81,  82,  83,  84,  85,  86,  87,  88,  89,  90,
        91,  92,  93,  94,  95,  96,  97,  98,  99, 100, 101, 102, 103,
       104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116,
       117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129,
       130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142,
       143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155,
       156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168,
       169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 18

In [23]:
data_y_df = pd.DataFrame(data_y,index=df_analyse.columns).T

In [24]:
data_y_df

date Afghanistan Albania Algeria Andorra Angola Antigua and Barbuda  \
0   2020-04-06         367     377    1423     525     16                  15   
1   2020-04-07         423     383    1468     545     17                  19   
2   2020-04-08         444     400    1572     564     19                  19   
3   2020-04-09         484     409    1666     583     19                  19   
4   2020-04-10         521     416    1761     601     19                  19   
5   2020-04-11         555     433    1825     601     19                  21   
6   2020-04-12         607     446    1914     638     19                  21   
7   2020-04-13         665     467    1983     646     19                  23   
8   2020-04-14         714     475    2070     659     19                  23   
9   2020-04-15         784     494    2160     673     19                  23   
10  2020-04-16         840     518    2268     673     19                  23   
11  2020-04-17         906     539    2418     696     19                  23   
12  2020-04-18         933     548    2534     704     24                  23   
13  2020-04-19         996     562    2629     713     24                  23   
14  2020-04-20        1026     584    2718     717     24                  23   
15  2020-04-21        1092     609    2811     717     24                  23   
16  2020-04-22        1176     634    2910     723     25                  24   
17  2020-04-23        1279     663    3007     723     25                  24   
18  2020-04-24        1351     678    3127     731     25                  24   
19  2020-04-25        1463     712    3256     738     25                  24   
20  2020-04-26        1531     726    3382     738     26                  24   
21  2020-04-27        1703     736    3517     743     27                  24   
22  2020-04-28        1828     750    3649     743     27                  24   
23  2020-04-29        1939     766    3848     743     27                  24   
24  2020-04-30        2171     773    4006     745     27                  24   
25  2020-05-01        2335     782    4154     745     30                  25   
26  2020-05-02        2469     789    4295     747     35                  25   
27  2020-05-03        2704     795    4474     748     35                  25   
28  2020-05-04        2894     803    4648     750     35                  25   
29  2020-05-05        3224     820    4838     751     36                  25   
30  2020-05-06        3392     832    4997     751     36                  25   
31  2020-05-07        3563     842    5182     752     36                  25   
32  2020-05-08        3778     850    5369     752     43                  25   
33  2020-05-09        4033     856    5558     754     43                  25   
34  2020-05-10        4402     868    5723     755     45                  25   
35  2020-05-11        4687     872    5891     755     45                  25   
36  2020-05-12        4963     876    6067     758     45                  25   
37  2020-05-13        5226     880    6253     760     45                  25   
38  2020-05-14        5639     898    6442     761     48                  25   
39  2020-05-15        6053     916    6629     761     48                  25   
40  2020-05-16        6402     933    6821     761     48                  25   
41  2020-05-17        6664     946    7019     761     48                  25   
42  2020-05-18        7072     948    7201     761     50                  25   
43  2020-05-19        7653     949    7377     761     52                  25   
44  2020-05-20        8145     964    7542     762     52                  25   
45  2020-05-21        8676     969    7728     762     58                  25   
46  2020-05-22        9216     981    7918     762     60                  25   
47  2020-05-23        9998     989    8113     762     61                  25   
48  2020-05-24       10582     998    830

In [25]:
data_y_df.to_csv('../ads_covid-19/data/processed/sir/ydata_SIR_data.csv',sep=';',index=False)

In [26]:
for column in data_y_df.columns[1:]:
    print(column)

Afghanistan
Albania
Algeria
Andorra
Angola
Antigua and Barbuda
Argentina
Armenia
Australia
Austria
Azerbaijan
Bahamas
Bahrain
Bangladesh
Barbados
Belarus
Belgium
Belize
Benin
Bhutan
Bolivia
Bosnia and Herzegovina
Botswana
Brazil
Brunei
Bulgaria
Burkina Faso
Burma
Burundi
Cabo Verde
Cambodia
Cameroon
Canada
Central African Republic
Chad
Chile
China
Colombia
Comoros
Congo (Brazzaville)
Congo (Kinshasa)
Costa Rica
Cote d'Ivoire
Croatia
Cuba
Cyprus
Czechia
Denmark
Diamond Princess
Djibouti
Dominica
Dominican Republic
Ecuador
Egypt
El Salvador
Equatorial Guinea
Eritrea
Estonia
Eswatini
Ethiopia
Fiji
Finland
France
Gabon
Gambia
Georgia
Germany
Ghana
Greece
Grenada
Guatemala
Guinea
Guinea-Bissau
Guyana
Haiti
Holy See
Honduras
Hungary
Iceland
India
Indonesia
Iran
Iraq
Ireland
Israel
Italy
Jamaica
Japan
Jordan
Kazakhstan
Kenya
Korea, South
Kosovo
Kuwait
Kyrgyzstan
Laos
Latvia
Lebanon
Lesotho
Liberia
Libya
Liechtenstein
Lithuania
Luxembourg
MS Zaandam
Madagascar
Malawi
Malaysia
Maldives
Mali
Mal

In [27]:
optimized_df = pd.DataFrame(columns = df_analyse.columns[1:],
                     index = ['opt_beta', 'opt_gamma', 'std_dev_error_beta', 'std_dev_error_gamma']) 

In [28]:
optimized_df

Afghanistan Albania Algeria Andorra Angola  \
opt_beta                    NaN     NaN     NaN     NaN    NaN   
opt_gamma                   NaN     NaN     NaN     NaN    NaN   
std_dev_error_beta          NaN     NaN     NaN     NaN    NaN   
std_dev_error_gamma         NaN     NaN     NaN     NaN    NaN   

                    Antigua and Barbuda Argentina Armenia Australia Austria  \
opt_beta                            NaN       NaN     NaN       NaN     NaN   
opt_gamma                           NaN       NaN     NaN       NaN     NaN   
std_dev_error_beta                  NaN       NaN     NaN       NaN     NaN   
std_dev_error_gamma                 NaN       NaN     NaN       NaN     NaN   

                    Azerbaijan Bahamas Bahrain Bangladesh Barbados Belarus  \
opt_beta                   NaN     NaN     NaN        NaN      NaN     NaN   
opt_gamma                  NaN     NaN     NaN        NaN      NaN     NaN   
std_dev_error_beta         NaN     NaN     NaN        NaN      NaN     NaN   
std_dev_error_gamma        NaN     NaN     NaN        NaN      NaN     NaN   

                    Belgium Belize Benin Bhutan Bolivia  \
opt_beta                NaN    NaN   NaN    NaN     NaN   
opt_gamma               NaN    NaN   NaN    NaN     NaN   
std_dev_error_beta      NaN    NaN   NaN    NaN     NaN   
std_dev_error_gamma     NaN    NaN   NaN    NaN     NaN   

                    Bosnia and Herzegovina Botswana Brazil Brunei Bulgaria  \
opt_beta                               NaN      NaN    NaN    NaN      NaN   
opt_gamma                              NaN      NaN    NaN    NaN      NaN   
std_dev_error_beta                     NaN      NaN    NaN    NaN      NaN   
std_dev_error_gamma                    NaN      NaN    NaN    NaN      NaN   

                    Burkina Faso Burma Burundi Cabo Verde Cambodia Cameroon  \
opt_beta                     NaN   NaN     NaN        NaN      NaN      NaN   
opt_gamma                    NaN   NaN     NaN        NaN      NaN      NaN   
std_dev_error_beta           NaN   NaN     NaN        NaN      NaN      NaN   
std_dev_error_gamma          NaN   NaN     NaN        NaN      NaN      NaN   

                    Canada Central African Republic Chad Chile China Colombia  \
opt_beta               NaN                      NaN  NaN   NaN   NaN      NaN   
opt_gamma              NaN                      NaN  NaN   NaN   NaN      NaN   
std_dev_error_beta     NaN                      NaN  NaN   NaN   NaN      NaN   
std_dev_error_gamma    NaN                      NaN  NaN   NaN   NaN      NaN   

                    Comoros Congo (Brazzaville) Congo (Kinshasa) Costa Rica  \
opt_beta                NaN                 NaN              NaN        NaN   
opt_gamma               NaN                 NaN              NaN        NaN   
std_dev_error_beta      NaN                 NaN              NaN        NaN   
std_dev_error_gamma     NaN                 NaN              NaN        NaN   

                    Cote d'Ivoire Croatia Cuba Cyprus Czechia Denmark  \
opt_beta                      NaN     NaN  NaN    NaN     NaN     NaN   
opt_gamma                     NaN     NaN  NaN    NaN     NaN     NaN   
std_dev_error_beta            NaN     NaN  NaN    NaN     NaN     NaN   
std_dev_error_gamma           NaN     NaN  NaN    NaN     NaN     NaN   

                    Diamond Princess Djibouti Dominica Dominican Republic  \
opt_beta                         NaN      NaN      NaN                NaN   
opt_gamma                        NaN      NaN      NaN                NaN   
std_dev_error_beta               NaN      NaN      NaN                NaN   
std_dev_error_gamma              NaN      NaN      NaN                NaN   

                    Ecuador Egypt El Salvador Equatorial Guinea Eritrea  \
opt_beta                NaN   NaN         NaN               NaN     NaN   
opt_gamma               NaN   NaN         NaN               NaN     NaN   
std_dev_error_beta      NaN   NaN       

In [29]:
def SIR_model_t(SIRN,t,beta,gamma):
    ''' Simple SIR model
        S: susceptible population
        t: time step, mandatory for integral.odeint
        I: infected people
        R: recovered people
        beta: 
        
        overall condition is that the sum of changes (differnces) sum up to 0
        dS+dI+dR=0
        S+I+R= N (constant size of population)
    
    '''
    
    S,I,R,N=SIRN
    dS_dt=-beta*S*I/N          #S*I is the 
    dI_dt=beta*S*I/N-gamma*I
    dR_dt=gamma*I
    dN_dt=0
    return dS_dt,dI_dt,dR_dt,dN_dt

In [30]:
def fit_odeint(t, beta, gamma):
#def fit_odeint(t, beta, gamma): #t==x?
    '''
    helper function for the integration
    '''
    return integrate.odeint(SIR_model_t, (S0, I0, R0, N0), t, args=(beta, gamma))[:,1] # we only would like to get dI

for i in range(N): t = Ridge(Xtrain, ytrain, .3) theta_Matrix.append(t) theta_Matrix = np.array(theta_Matrix)



In [31]:

t = []
fitted_final_data = []
#popt=[0.4,0.1]
global I0, N0, S0, R0
for column in data_y_df.columns[1:]:
    I0 = data_y_df[column].loc[0]
    N0 = population_df[column].loc['population']
    S0 = N0-I0
    R0 = 0
    t  = np.arange(len(data_y_df[column]))
    #print(I0,S0,R0,N0)
    #print(t)
    popt=[0.4,0.1]
    #yd = fit_odeint(t, *popt)
    #yd_data.append(yd)
    #fit_ode_data.append(np.array(fit_odeint(t, *popt)))
    fit_odeint(t, *popt)
    
    
    popt, pcov = optimize.curve_fit(fit_odeint, t, data_y_df[column], maxfev=5000)
    perr = np.sqrt(np.diag(pcov))
   
    
    optimized_df.at['opt_beta', column] = popt[0]
    optimized_df.at['opt_gamma', column] = popt[1]
    optimized_df.at['std_dev_error_beta', column] = perr[0]
    optimized_df.at['std_dev_error_gamma', column] = perr[1]
    
    fitted = fit_odeint(t, *popt)
    fitted_final_data.append(np.array(fitted))
    #print('standard deviation errors : ',str(perr), ' start infect:',ydata[0])
    #print("Optimal parameters: beta =", popt[0], " and gamma = ", popt[1])
#yd_data =  np.array(yd_data)
    

/opt/anaconda3/envs/EnterpriseDataScience/lib/python3.7/site-packages/scipy/optimize/minpack.py:829: OptimizeWarning: Covariance of the parameters could not be estimated
  category=OptimizeWarning)
/opt/anaconda3/envs/EnterpriseDataScience/lib/python3.7/site-packages/ipykernel_launcher.py:17: RuntimeWarning: overflow encountered in double_scalars
/opt/anaconda3/envs/EnterpriseDataScience/lib/python3.7/site-packages/ipykernel_launcher.py:18: RuntimeWarning: overflow encountered in double_scalars
/opt/anaconda3/envs/EnterpriseDataScience/lib/python3.7/site-packages/scipy/integrate/odepack.py:247: ODEintWarning: Excess work done on this call (perhaps wrong Dfun type). Run with full_output = 1 to get quantitative information.
  warnings.warn(warning_msg, ODEintWarning)


In [32]:
fitted_final_data

[array([  367.        ,   385.88764516,   405.74293293,   426.61497079,
          448.55530923,   471.61805786,   495.86000554,   521.34074926,
          548.12282371,   576.27183946,   605.85662497,   636.94937454,
          669.62580318,   703.9653061 ,   740.05112505,   777.97052005,
          817.81494792,   859.6802466 ,   903.66682583,   949.87986344,
          998.42950888,  1049.4310926 ,  1103.00534175,  1159.27859812,
         1218.38304685,  1280.45694965,  1345.64487599,  1414.09794852,
         1485.97408878,  1561.43825977,  1640.66272314,  1723.82729118,
         1811.11957355,  1902.73523998,  1998.87826876,  2099.76118841,
         2205.60533476,  2316.64108115,  2433.10806284,  2555.255411  ,
         2683.34194454,  2817.63635961,  2958.41741573,  3105.97406267,
         3260.60556971,  3422.62163069,  3592.34239093,  3770.09848127,
         3956.23099831,  4151.09138671,  4355.04133127,  4568.45255578,
         4791.70650586,  5025.19403719,  5269.31496322,  5524.47

In [33]:
optimized_df.to_csv('../ads_covid-19/data/processed/sir/optimized_SIR_data.csv',sep=';',index=False)

In [34]:
t

array([  0,   1,   2,   3,   4,   5,   6,   7,   8,   9,  10,  11,  12,
        13,  14,  15,  16,  17,  18,  19,  20,  21,  22,  23,  24,  25,
        26,  27,  28,  29,  30,  31,  32,  33,  34,  35,  36,  37,  38,
        39,  40,  41,  42,  43,  44,  45,  46,  47,  48,  49,  50,  51,
        52,  53,  54,  55,  56,  57,  58,  59,  60,  61,  62,  63,  64,
        65,  66,  67,  68,  69,  70,  71,  72,  73,  74,  75,  76,  77,
        78,  79,  80,  81,  82,  83,  84,  85,  86,  87,  88,  89,  90,
        91,  92,  93,  94,  95,  96,  97,  98,  99, 100, 101, 102, 103,
       104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116,
       117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129,
       130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142,
       143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155,
       156, 157, 158, 159, 160, 161])

In [35]:
fitted_SIR_data_df = pd.DataFrame(fitted_final_data,index=df_analyse.columns[1:]).T

In [36]:
fitted_SIR_data_df.head()

Afghanistan     Albania      Algeria     Andorra     Angola  \
0   367.000000  377.000000  1423.000000  525.000000  16.000000   
1   385.887645  387.419335  1465.485068  528.456152  16.620361   
2   405.742933  398.119957  1509.217598  531.927870  17.264721   
3   426.614971  409.109082  1554.232937  535.415116  17.934005   
4   448.555309  420.394091  1600.567358  538.917852  18.629172   

   Antigua and Barbuda    Argentina     Armenia    Australia       Austria  \
0            15.000000  1554.000000  833.000000  5797.000000  12297.000000   
1            15.268030  1621.395729  868.283812  5918.671770  12361.298800   
2            15.540416  1691.709776  905.045816  6041.515970  12425.933716   
3            15.817213  1765.068102  943.346519  6165.471272  12490.906504   
4            16.098474  1841.602068  983.248786  6290.472296  12556.218930   

   Azerbaijan    Bahamas     Bahrain  Bangladesh   Barbados     Belarus  \
0  641.000000  29.000000  756.000000  123.000000  60.000000  700.000000   
1  666.958526  29.902166  787.490467  131.663548  60.407128  737.140427   
2  693.958264  30.832297  820.281652  140.937191  60.817019  776.242057   
3  722.040146  31.791251  854.426345  150.863877  61.229691  817.407426   
4  751.246644  32.779916  889.979400  161.489569  61.645163  860.744321   

        Belgium    Belize      Benin    Bhutan     Bolivia  \
0  20814.000000  7.000000  26.000000  5.000000  183.000000   
1  22349.446285  7.268838  27.127581  5.142958  193.399250   
2  23952.786583  7.547858  28.303757  5.289967  204.388938   
3  25619.236973  7.837434  29.530594  5.441138  216.002527   
4  27342.490455  8.137955  30.810246  5.596588  228.275370   

   Bosnia and Herzegovina  Botswana        Brazil      Brunei    Bulgaria  \
0              674.000000  6.000000  12161.000000  135.000000  549.000000   
1              691.501873  6.259757  12793.396053  135.106417  565.187177   
2              709.452914  6.530744  13457.831890  135.212217  581.843421   
3              727.864372  6.813445  14155.839658  135.317397  598.981829   
4              746.747760  7.108367  14889.014909  135.421954  616.615836   

   Burkina Faso      Burma   Burundi  Cabo Verde    Cambodia    Cameroon  \
0    364.000000  22.000000  3.000000    7.000000  114.000000  658.000000   
1    369.005224  22.608301  3.142862    7.382421  114.631602  682.114990   
2    374.066653  23.233420  3.292504    7.785713  115.266689  707.097784   
3    379.184538  23.875823  3.449244    8.211015  115.905278  732.978412   
4    384.359120  24.535987  3.613418    8.659523  116.547390  759.787847   

         Canada  Central African Republic       Chad        Chile  \
0  16563.000000                  8.000000   9.000000  5009.000000   
1  17005.912591                  8.518485   9.306607  5243.728288   
2  17459.780129                  9.070548   9.623653  5489.382564   
3  17924.823941                  9.658361   9.951491  5746.464319   
4  18401.266988                 10.284235  10.290489  6015.497386   

          China     Colombia  Comoros  Congo (Brazzaville)  Congo (Kinshasa)  \
0  82665.000000  1579.000000      0.0            45.000000        161.000000   
1  82705.369191  1655.252939      0.0            46.862021        168.081269   
2  82745.758095  1735.183328      0.0            48.800663        175.471485   
3  82786.166724  1818.968027      0.0            50.819044        183.183900   
4  82826.595086  1906.792359      0.0            52.920404        191.232314   

   Costa Rica  Cote d'Ivoire      Croatia        Cuba      Cyprus  \
0  467.000000     323.000000  1222.000000  350.000000  465.000000   
1  484.843385     336.162457  1239.089731  358.228326  470.182920   
2  503.363041     349.856249  1256.418463  366.640203  475.410029   
3  522.584171     364.102406  1273.989537  375.239242  480.681365   
4  542.532880     378.922751  1291.806344  384.029105  485.996953   

       Czechia      Denmark  Diamond Princess    Djibouti   Dominica  \
0  4822.00

In [37]:
fitted_SIR_data_df.to_csv('../ads_covid-19/data/processed/sir/fitted_SIR_data.csv',sep=';',index=False)

#reqd_pop_list.to_csv('C:/ProgramData/Anaconda3/eps_covid19/data/processed/population_data.csv',sep=';',index=False)

# Implementation of Dash

In [38]:
import pandas as pd
import numpy as np
import dash
dash.__version__
import dash_core_components as dcc
import dash_html_components as html
from dash.dependencies import Input, Output,State

import plotly.graph_objects as go

import os
print(os.getcwd())

/Users/anweshapanda/Enterprise Data Science


In [39]:
fitted_final_data_dash_df = pd.read_csv('../ads_covid-19/data/processed/sir/fitted_SIR_data.csv',sep=';')

In [40]:
fitted_final_data_dash_df

Afghanistan      Albania       Algeria      Andorra       Angola  \
0      367.000000   377.000000   1423.000000   525.000000    16.000000   
1      385.887645   387.419335   1465.485068   528.456152    16.620361   
2      405.742933   398.119957   1509.217598   531.927870    17.264721   
3      426.614971   409.109082   1554.232937   535.415116    17.934005   
4      448.555309   420.394091   1600.567358   538.917852    18.629172   
5      471.618058   431.982529   1648.258076   542.436037    19.351218   
6      495.860006   443.882110   1697.343266   545.969627    20.101177   
7      521.340749   456.100721   1747.862087   549.518578    20.880123   
8      548.122824   468.646420   1799.854697   553.082842    21.689170   
9      576.271839   481.527440   1853.362274   556.662371    22.529473   
10     605.856625   494.752194   1908.427035   560.257113    23.402234   
11     636.949375   508.329273   1965.092258   563.867015    24.308699   
12     669.625803   522.267450   2023.402296   567.492022    25.250160   
13     703.965306   536.575682   2083.402602   571.132076    26.227959   
14     740.051125   551.263111   2145.139741   574.787118    27.243491   
15     777.970520   566.339067   2208.661417   578.457085    28.298199   
16     817.814948   581.813068   2274.016481   582.141915    29.393584   
17     859.680247   597.694823   2341.254961   585.841539    30.531202   
18     903.666826   613.994230   2410.428069   589.555891    31.712670   
19     949.879863   630.721382   2481.588224   593.284900    32.939661   
20     998.429509   647.886565   2554.789067   597.028492    34.213916   
21    1049.431093   665.500258   2630.085477   600.786592    35.537237   
22    1103.005342   683.573134   2707.533587   604.559122    36.911498   
23    1159.278598   702.116064   2787.190797   608.346004    38.338638   
24    1218.383047   721.140111   2869.115790   612.147154    39.820672   
25    1280.456950   740.656533   2953.368543   615.962487    41.359689   
26    1345.644876   760.676783   3040.010339   619.791918    42.957856   
27    1414.097949   781.212508   3129.103780   623.635355    44.617419   
28    1485.974089   802.275545   3220.712797   627.492708    46.340709   
29    1561.438260   823.877923   3314.902651   631.363882    48.130144   
30    1640.662723   846.031861   3411.739947   635.248780    49.988227   
31    1723.827291   868.749762   3511.292639   639.147303    51.917559   
32    1811.119574   892.044218   3613.630031   643.059349    53.920833   
33    1902.735240   915.927997   3718.822776   646.984814    56.000840   
34    1998.878269   940.414048   3826.942883   650.923590    58.160477   
35    2099.761188   965.515491   3938.063712   654.875569    60.402744   
36    2205.605335   991.245618   4052.259962   658.840639    62.730750   
37    2316.641081  1017.617884   4169.607672   662.818684    65.147718   
38    2433.108063  1044.645901   4290.184215   666.809588    67.656988   
39    2555.255411  1072.343437   4414.068271   670.813230    70.262019   
40    2683.341945  1100.724403   4541.339822   674.829489    72.966397   
41    2817.636360  1129.802849   4672.080137   678.858239    75.773835   
42    2958.417416  1159.592954   4806.371738   682.899352    78.688179   
43    3105.974063  1190.109021   4944.298378   686.952698    81.713413   
44    3260.605570  1221.365463   5085.945018   691.018143    84.853660   
45    3422.621631  1253.376793   5231.397793   695.095553    88.113193   
46    3592.342391  1286.157615   5380.743955   699.184787    91.496432   
47    3770.098481  1319.722613   5534.071856   703.285705    95.007954   
48    3956.230998  1354.086534   5691.470895   707.398163    98.652495   
49    4151.091387  1389.264174   5853.031443   711.522014   102.434958   
50    4355.041331  1425.270370   6018.844813   715.657107   106.360412   
51    4568.452556  1462.119976   6189.003189   719.803291   110.434105   
52    4791.706506  1499.827850   6363.599544   723.960411   114.661461   
53    5025

In [41]:
yd = fitted_final_data_dash_df.copy()

In [ ]:
# Initial reading of required data
#df_input_large=pd.read_csv('../ads_covid-19/data/processed/COVID_final_set.csv',sep=';')
fitted_final_data_dash_df = pd.read_csv('../ads_covid-19/data/processed/SIR/fitted_SIR_data.csv',sep=';')
optimized_dash_df = pd.read_csv('../ads_covid-19/data/processed/SIR/optimized_SIR_data.csv',sep=';')
ydata_dash_df = pd.read_csv('../ads_covid-19/data/processed/SIR/ydata_SIR_data.csv',sep=';')



fig = go.Figure()

app = dash.Dash()
app.layout = html.Div([

    dcc.Markdown('''
    #  Applied Data Science on COVID-19 data
    Goal of the project is to learn data science by applying a cross industry standard process,
    it covers the full walkthrough of: automated data gathering, data transformations,
    filtering and machine learning to approximating the doubling time, and
    (static) deployment of responsive dashboard.
    '''),

    dcc.Markdown('''
    ## Multi-Select Country for visualization
    '''),
    
    dcc.Dropdown(
        id='country_drop_down',
        options=[ {'label': each,'value':each} for each in fitted_final_data_dash_df],
        value=['US', 'Germany','Italy'], # which are pre-selected
        multi=True
    ),
    
    dcc.Markdown('''
        ## Select SIR Model and/or fitted SIR Model
        '''),
    
    dcc.Dropdown(
    id='doubling_time',
    options=[
        {'label': 'SIR curve and fitted SIR curve ', 'value': 'SIR_value'},
        #{'label': 'Fitted SIR curve', 'value': 'Fitted_SIR_curve'},
        #{'label': 'Timeline Doubling Rate', 'value': 'confirmed_DR'},
        #{'label': 'Timeline Doubling Rate Filtered', 'value': 'confirmed_filtered_DR'},
    ],
    value='SIR_value',
    multi=False
    ),

    dcc.Graph(figure=fig, id='main_window_slope')
])


@app.callback(
    Output('main_window_slope', 'figure'),
    [Input('country_drop_down', 'value'),
    Input('doubling_time', 'value')])
def update_figure(full_country_list,show_doubling):
    
    #if 'SIR' in show_doubling:
    #    my_yaxis={'type':"log",
    #       'title':'Fit of SIR model for '+str(each)+' cases'
    #      }
    #else:
    #my_yaxis={'type':"log",
    #          'title':'Confirmed infected people (source johns hopkins csse, log-scale)'
    #      }



    traces = []
    for each in full_country_list:
        #traces = []

        #df_plot=df_input_large[df_input_large['country']==each]
        if show_doubling=='SIR_value':
            yd = ydata_dash_df.copy()
        else:
            yd = fitted_final_data_dash_df.copy()

        #if show_doubling=='doubling_rate_filtered':
        #    df_plot=df_plot[['state','country','confirmed','confirmed_filtered','confirmed_DR','confirmed_filtered_DR','date']].groupby(['country','date']).agg(np.mean).reset_index()
        #else:
        #    df_plot=df_plot[['state','country','confirmed','confirmed_filtered','confirmed_DR','confirmed_filtered_DR','date']].groupby(['country','date']).agg(np.sum).reset_index()
        #print(show_doubling)


        traces.append(dict(x=t, #df_plot.date,
                                y=ydata_dash_df[each], #=df_plot[show_doubling],
                                mode='markers+lines',
                                opacity=0.9,
                                line_width=2,
                                marker_size=4,
                                name=each
                           
                        )
                )
        traces.append(dict(x=t, #df_plot.date,
                                y=fitted_final_data_dash_df[each], #=df_plot[show_doubling],
                                mode='markers+lines',
                                opacity=0.9,
                                line_width=2,
                                marker_size=4,
                                name=each+'_fitted'
                           
                        )
                )
        

    return {
            'data': traces,
            'layout': dict (
                width=1280,
                height=720,

                xaxis={'title':'Timeline',
                        'tickangle':-45,
                        'nticks':20,
                        'tickfont':dict(size=14,color="#7f7f7f"),
                      },

                yaxis={'type': 'log',
                        'range': '[1.1,5.5]'
                        }
                #yaxis=my_yaxis
        )
    }

if __name__ == '__main__':

    app.run_server(debug=True, host='127.0.0.1', port = 8051, use_reloader=False)
    app.run_server(debug=True, use_reloader=False)




    

Dash is running on http://127.0.0.1:8051/

 in production, use a production WSGI server like gunicorn instead.

 * Serving Flask app "__main__" (lazy loading)
 * Environment: production
   Use a production WSGI server instead.
 * Debug mode: on
